<a href="https://colab.research.google.com/github/khangtruong2252314/ML-BackProg/blob/main/ML_A1.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

## Login

In [ ]:
from huggingface_hub import login
from google.colab import userdata

mail = userdata.get('MAIL')
user = userdata.get('USER')
token = userdata.get('GIT_TOKEN')
!git config --global user.email {mail}
!git config --global user.name {user}

### Git clone

In [ ]:
!git clone https://{token}@github.com/khangtruong2252314/ML-BackProg

Cloning into 'ML-BackProg'...
remote: Enumerating objects: 196, done.
remote: Counting objects: 100% (196/196), done.
remote: Compressing objects: 100% (174/174), done.
remote: Total 196 (delta 66), reused 39 (delta 6), pack-reused 0 (from 0)
Receiving objects: 100% (196/196), 14.70 MiB | 11.24 MiB/s, done.
Resolving deltas: 100% (66/66), done.


In [ ]:
%cd ML-BackProg

/content/ML-BackProg


## Load dataset

In [ ]:
import pandas as pd

splits = {'train': 'plain_text/train-00000-of-00001.parquet', 'test': 'plain_text/test-00000-of-00001.parquet', 'unsupervised': 'plain_text/unsupervised-00000-of-00001.parquet'}
df = pd.read_parquet("hf://datasets/stanfordnlp/imdb/" + splits["train"])

/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


## Run

### Imports

In [ ]:
import pandas as pd
from sklearn.model_selection import train_test_split, RandomizedSearchCV
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.tree import DecisionTreeClassifier
from sklearn.pipeline import Pipeline
from sklearn.model_selection import GridSearchCV
from sklearn.metrics import classification_report
from scipy.stats import randint

In [ ]:
# Separate features and labels
X = df['text']
y = df['label']

# Split data into training and testing
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

### Model

#### Decision tree

In [ ]:
# Pipeline for text vectorization and decision tree
pipeline = Pipeline([
    ('tfidf', TfidfVectorizer(max_features=5000)),
    ('tree', DecisionTreeClassifier(random_state=42))
])

# Define the parameter distributions to sample from
param_dist = {
    'tree__max_depth': randint(10, 40),
    'tree__min_samples_split': randint(2, 11),
    'tree__min_samples_leaf': randint(1, 5)
}

# Randomized search with cross-validation
random_search = RandomizedSearchCV(pipeline, param_distributions=param_dist,
                                   n_iter=10, cv=3, verbose=1, random_state=42)

# Fit the model
random_search.fit(X_train, y_train)

# Print best parameters
print(f"Best parameters: {random_search.best_params_}")

# Generate predictions
y_pred = random_search.predict(X_test)

# Print classification report
print(classification_report(y_test, y_pred))

Fitting 3 folds for each of 10 candidates, totalling 30 fits
Best parameters: {'tree__max_depth': 16, 'tree__min_samples_leaf': 4, 'tree__min_samples_split': 9}
              precision    recall  f1-score   support

           0       0.77      0.62      0.69      2515
           1       0.68      0.82      0.74      2485

    accuracy                           0.72      5000
   macro avg       0.73      0.72      0.72      5000
weighted avg       0.73      0.72      0.72      5000



In [ ]:
from joblib import dump, load

# Save the model
dump(random_search, 'ml-course/models/trained/decision_tree.joblib')
print("Model saved successfully!")

# Load the model
loaded_model = load('ml-course/models/trained/decision_tree.joblib')
print("Model loaded successfully!")

# Make predictions with the loaded model
y_pred_loaded = loaded_model.predict(X_test)
print(classification_report(y_test, y_pred_loaded))

Model saved successfully!
Model loaded successfully!
              precision    recall  f1-score   support

           0       0.77      0.62      0.69      2515
           1       0.68      0.82      0.74      2485

    accuracy                           0.72      5000
   macro avg       0.73      0.72      0.72      5000
weighted avg       0.73      0.72      0.72      5000





```
# This is formatted as code
```

#### ANN

In [ ]:
from sklearn.feature_extraction.text import TfidfVectorizer

# Create a TfidfVectorizer instance
vectorizer = TfidfVectorizer(max_features=5000)  # You can adjust max_features

# Fit the vectorizer to the training data and transform it
X_train_tfidf = vectorizer.fit_transform(X_train)

# Transform the test data using the fitted vectorizer
X_test_tfidf = vectorizer.transform(X_test)

In [ ]:
from sklearn.neural_network import MLPClassifier

# Create an MLPClassifier instance
mlp = MLPClassifier(hidden_layer_sizes=(100,), activation='relu', solver='adam',
                    max_iter=500, random_state=42)

# Train the model
mlp.fit(X_train_tfidf, y_train)

# Make predictions
y_pred = mlp.predict(X_test_tfidf)

# Evaluate the model
print(classification_report(y_test, y_pred))

# Save the model
dump(mlp, 'ml-course/models/trained/ann_sklearn.joblib')
print("ANN (sklearn) model saved successfully!")

              precision    recall  f1-score   support

           0       0.85      0.84      0.85      2515
           1       0.84      0.85      0.85      2485

    accuracy                           0.85      5000
   macro avg       0.85      0.85      0.85      5000
weighted avg       0.85      0.85      0.85      5000

ANN (sklearn) model saved successfully!


#### Naive Bayes

In [ ]:
import numpy as np
from sklearn.naive_bayes import MultinomialNB
from sklearn.metrics import accuracy_score, classification_report
from scipy.sparse import csr_matrix
import random
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.feature_extraction.text import TfidfVectorizer

# Load dataset
splits = {'train': 'plain_text/train-00000-of-00001.parquet'}
df = pd.read_parquet("hf://datasets/stanfordnlp/imdb/" + splits["train"])

# Separate features and labels
X = df['text']
y = df['label']

# Split data
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# TF-IDF Vectorization
vectorizer = TfidfVectorizer(max_features=5000)
X_train_tfidf = vectorizer.fit_transform(X_train)
X_test_tfidf = vectorizer.transform(X_test)

print("Shape of feature vectors:", X_train_tfidf.shape)
# Initialize Multinomial Naive Bayes with Laplace smoothing
nb_classifier = MultinomialNB(alpha=1.0)

# Train the model
nb_classifier.fit(X_train_tfidf, y_train)

# Make predictions
y_pred = nb_classifier.predict(X_test_tfidf)

# Evaluate the model
print("Naive Bayes Results:")
print("Accuracy:", accuracy_score(y_test, y_pred))
print("\nClassification Report:")
print(classification_report(y_test, y_pred))

# === Genetic Algorithm for Feature Selection ===
class GeneticAlgorithmFeatureSelector:
    def __init__(self, population_size=50, num_generations=20,
                 mutation_rate=0.1, num_features=2000):
        self.population_size = population_size
        self.num_generations = num_generations
        self.mutation_rate = mutation_rate
        self.num_features = num_features
        self.vectorizer = vectorizer
        self.classifier = MultinomialNB(alpha=1.0)

    # 1. Feature encoding (binary mask: 1=feature selected, 0=feature discarded)
    def initialize_population(self):
        return [np.random.randint(0, 2, self.num_features)
                for _ in range(self.population_size)]

    # 2. Fitness function (classification accuracy)
    def fitness(self, individual, X_train, X_test, y_train, y_test):
        # Apply feature mask to sparse matrices
        selected_features = np.where(individual == 1)[0]
        if len(selected_features) == 0:  # Prevent empty feature set
            return 0.0

        X_train_selected = X_train[:, selected_features]
        X_test_selected = X_test[:, selected_features]

        # Train and evaluate
        self.classifier.fit(X_train_selected, y_train)
        y_pred = self.classifier.predict(X_test_selected)
        return accuracy_score(y_test, y_pred)

    # 3. Crossover operator (single-point crossover)
    def crossover(self, parent1, parent2):
        crossover_point = random.randint(1, self.num_features-1)
        child1 = np.concatenate([parent1[:crossover_point], parent2[crossover_point:]])
        child2 = np.concatenate([parent2[:crossover_point], parent1[crossover_point:]])
        return child1, child2

    # 4. Mutation operator
    def mutate(self, individual):
        for i in range(len(individual)):
            if random.random() < self.mutation_rate:
                individual[i] = 1 - individual[i]  # Flip 0 to 1 or 1 to 0
        return individual

    # 5. Selection strategy (tournament selection)
    def tournament_selection(self, population, fitness_scores, tournament_size=3):
        tournament = random.sample(list(zip(population, fitness_scores)), tournament_size)
        return max(tournament, key=lambda x: x[1])[0]

    # Main GA loop
    def evolve(self, X_train, X_test, y_train, y_test):
        population = self.initialize_population()
        best_fitness_history = []

        for generation in range(self.num_generations):
            # Calculate fitness for all individuals
            fitness_scores = [self.fitness(ind, X_train, X_test, y_train, y_test)
                            for ind in population]

            # Track best solution
            best_idx = np.argmax(fitness_scores)
            best_fitness = fitness_scores[best_idx]
            best_individual = population[best_idx]
            best_fitness_history.append(best_fitness)

            print(f"Generation {generation+1}/{self.num_generations} - "
                  f"Best Fitness: {best_fitness:.4f}")

            # Create new population
            new_population = [best_individual]  # Elitism: keep best solution

            while len(new_population) < self.population_size:
                # Selection
                parent1 = self.tournament_selection(population, fitness_scores)
                parent2 = self.tournament_selection(population, fitness_scores)

                # Crossover
                child1, child2 = self.crossover(parent1, parent2)

                # Mutation
                child1 = self.mutate(child1)
                child2 = self.mutate(child2)

                new_population.extend([child1, child2])

            population = new_population[:self.population_size]  # Truncate to population size

        # Final evaluation
        best_features = np.where(best_individual == 1)[0]
        print(f"\nBest solution - Number of selected features: {len(best_features)}")
        return best_individual, best_fitness_history

# Run Genetic Algorithm
ga = GeneticAlgorithmFeatureSelector(
    population_size=100,
    num_generations=50,
    mutation_rate=0.1,
    num_features=5000
)

best_features, fitness_history = ga.evolve(
    X_train_tfidf, X_test_tfidf, y_train, y_test
)

# Final model with selected features
final_X_train = X_train_tfidf[:, np.where(best_features == 1)[0]]
final_X_test = X_test_tfidf[:, np.where(best_features == 1)[0]]
final_classifier = MultinomialNB(alpha=1.0)
final_classifier.fit(final_X_train, y_train)
final_predictions = final_classifier.predict(final_X_test)

print("\nFinal Model Results with GA-selected features:")
print("Accuracy:", accuracy_score(y_test, final_predictions))
print("Classification Report:")
print(classification_report(y_test, final_predictions))

Shape of feature vectors: (20000, 5000)
Naive Bayes Results:
Accuracy: 0.8516

Classification Report:
              precision    recall  f1-score   support

           0       0.85      0.85      0.85      2515
           1       0.85      0.85      0.85      2485

    accuracy                           0.85      5000
   macro avg       0.85      0.85      0.85      5000
weighted avg       0.85      0.85      0.85      5000

Generation 1/50 - Best Fitness: 0.8352
Generation 2/50 - Best Fitness: 0.8356
Generation 3/50 - Best Fitness: 0.8410
Generation 4/50 - Best Fitness: 0.8414
Generation 5/50 - Best Fitness: 0.8422
Generation 6/50 - Best Fitness: 0.8436
Generation 7/50 - Best Fitness: 0.8462
Generation 8/50 - Best Fitness: 0.8462
Generation 9/50 - Best Fitness: 0.8482
Generation 10/50 - Best Fitness: 0.8482
Generation 11/50 - Best Fitness: 0.8482
Generation 12/50 - Best Fitness: 0.8482
Generation 13/50 - Best Fitness: 0.8506
Generation 14/50 - Best Fitness: 0.8506
Generation 15/50 - B

#### Graphical Models (Bayesian Networks, HMM)

In [ ]:
import pandas as pd
import numpy as np
from pgmpy.models import BayesianNetwork
from pgmpy.estimators import MaximumLikelihoodEstimator
from pgmpy.sampling import BayesianModelSampling
from sklearn.model_selection import train_test_split
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.preprocessing import KBinsDiscretizer
from sklearn.feature_selection import SelectKBest, mutual_info_classif
from sklearn.metrics import classification_report, accuracy_score, confusion_matrix
from joblib import Parallel, delayed
import multiprocessing
from hmmlearn import hmm

# Load dataset
splits = {'train': 'plain_text/train-00000-of-00001.parquet'}
df = pd.read_parquet("hf://datasets/stanfordnlp/imdb/" + splits["train"])

# Separate features and labels
X = df['text']
y = df['label']

# Split data
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# TF-IDF Vectorization
vectorizer = TfidfVectorizer(max_features=2000)
X_train_tfidf = vectorizer.fit_transform(X_train)
X_test_tfidf = vectorizer.transform(X_test)

print("Shape of feature vectors:", X_train_tfidf.shape)

# Discretize features
n_bins = 5
discretizer = KBinsDiscretizer(n_bins=n_bins, encode='ordinal', strategy='uniform')
X_train_discrete = discretizer.fit_transform(X_train_tfidf.toarray())
X_test_discrete = discretizer.transform(X_test_tfidf.toarray())

# Feature selection
selector = SelectKBest(mutual_info_classif, k=20)
X_train_selected = selector.fit_transform(X_train_discrete, y_train)
X_test_selected = selector.transform(X_test_discrete)

# Convert to DataFrame
feature_names = [f'feature_{i}' for i in range(X_train_selected.shape[1])]
train_df = pd.DataFrame(X_train_selected, columns=feature_names)
train_df['label'] = y_train.values

# Define Bayesian Network structure
edges = [
    ('feature_0', 'feature_1'),
    ('feature_1', 'feature_2'),
    ('feature_2', 'feature_3'),
    ('feature_3', 'feature_4'),
    ('feature_4', 'feature_5'),
    ('feature_5', 'feature_6'),
    ('feature_6', 'feature_7'),
    ('feature_7', 'feature_8'),
    ('feature_8', 'feature_9'),
    ('feature_9', 'feature_10'),
    ('feature_10', 'feature_11'),
    ('feature_11', 'feature_12'),
    ('feature_12', 'feature_13'),
    ('feature_13', 'feature_14'),
    ('feature_14', 'feature_15'),
    ('feature_15', 'feature_16'),
    ('feature_16', 'feature_17'),
    ('feature_17', 'feature_18'),
    ('feature_18', 'feature_19'),
    ('feature_19', 'label')
]
model = BayesianNetwork(edges)

# Fit the model with corrected column selection
relevant_columns = [edge[0] for edge in edges] + ['label']  # All features involved in edges plus label
relevant_columns = list(set(relevant_columns))  # Remove duplicates
try:
    model.fit(train_df[relevant_columns], estimator=MaximumLikelihoodEstimator)
except ValueError as e:
    print(f"Error fitting model: {e}")
    # Fallback to simpler structure
    edges = [('feature_0', 'label')]
    model = BayesianNetwork(edges)
    model.fit(train_df[['feature_0', 'label']], estimator=MaximumLikelihoodEstimator)

# Sampling for predictions
sampler = BayesianModelSampling(model)
n_samples = 2000

def predict_bayesian(row):
    # Only use features that are in the model
    evidence = {}
    for feat in feature_names[:20]:
        if feat in [e[0] for e in model.edges()]:  # Check if feature is in model
            evidence[feat] = row[feature_names.index(feat)]
    try:
        samples = sampler.forward_sample(size=n_samples, evidence=evidence)
        return samples['label'].mode()[0]
    except Exception as e:
        print(f"Sampling error: {e}")
        return np.random.choice([0, 1])  # Fallback

# Parallel predictions
n_cores = multiprocessing.cpu_count()
y_pred = Parallel(n_jobs=n_cores)(
    delayed(predict_bayesian)(X_test_selected[i]) for i in range(len(X_test_selected))
)

# Evaluate Bayesian Network
print("\nBayesian Network Results:")
print("Accuracy:", accuracy_score(y_test, y_pred))
print("\nClassification Report:")
print(classification_report(y_test, y_pred))
print("\nConfusion Matrix:")
print(confusion_matrix(y_test, y_pred))

# HMM Implementation
def create_sequences(X, sequence_length=10):
    sequences = []
    for i in range(X.shape[0]):
        seq = X[i].toarray().flatten()
        if len(seq) < sequence_length:
            seq = np.pad(seq, (0, sequence_length - len(seq)))
        elif len(seq) > sequence_length:
            seq = seq[:sequence_length]
        sequences.append(seq)
    return np.array(sequences)

sequence_length = 10
X_train_seq = create_sequences(X_train_tfidf, sequence_length)
X_test_seq = create_sequences(X_test_tfidf, sequence_length)

n_components = 3
hmm_positive = hmm.GaussianHMM(n_components=n_components, covariance_type="diag")
hmm_negative = hmm.GaussianHMM(n_components=n_components, covariance_type="diag")

positive_idx = y_train == 1
negative_idx = y_train == 0

hmm_positive.fit(X_train_seq[positive_idx])
hmm_negative.fit(X_train_seq[negative_idx])

def hmm_predict(X):
    predictions = []
    for sequence in X:
        pos_score = hmm_positive.score(sequence.reshape(1, -1))
        neg_score = hmm_negative.score(sequence.reshape(1, -1))
        predictions.append(1 if pos_score > neg_score else 0)
    return np.array(predictions)

y_pred_hmm = hmm_predict(X_test_seq)

# Evaluate HMM
print("\nHMM Results:")
print("Accuracy:", accuracy_score(y_test, y_pred_hmm))
print("\nClassification Report:")
print(classification_report(y_test, y_pred_hmm))
print("\nConfusion Matrix:")
print(confusion_matrix(y_test, y_pred_hmm))

Shape of feature vectors: (20000, 2000)

Bayesian Network Results:
Accuracy: 0.5186

Classification Report:
              precision    recall  f1-score   support

           0       0.52      0.51      0.52      2515
           1       0.52      0.53      0.52      2485

    accuracy                           0.52      5000
   macro avg       0.52      0.52      0.52      5000
weighted avg       0.52      0.52      0.52      5000


Confusion Matrix:
[[1281 1234]
 [1173 1312]]

HMM Results:
Accuracy: 0.5096

Classification Report:
              precision    recall  f1-score   support

           0       0.55      0.13      0.22      2515
           1       0.50      0.89      0.64      2485

    accuracy                           0.51      5000
   macro avg       0.53      0.51      0.43      5000
weighted avg       0.53      0.51      0.43      5000


Confusion Matrix:
[[ 336 2179]
 [ 273 2212]]

Model Comparison:
Bayesian Network Accuracy: 0.5186
HMM Accuracy: 0.5096


In [ ]:
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.feature_extraction.text import TfidfVectorizer
from pgmpy.models import BayesianNetwork
from pgmpy.estimators import MaximumLikelihoodEstimator
from pgmpy.inference import VariableElimination
from sklearn.preprocessing import KBinsDiscretizer
from sklearn.metrics import accuracy_score

# Load dataset
splits = {'train': 'plain_text/train-00000-of-00001.parquet'}
df = pd.read_parquet("hf://datasets/stanfordnlp/imdb/" + splits["train"])

# Separate features and labels
X = df['text']
y = df['label']

# Split data
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# TF-IDF Vectorization
vectorizer = TfidfVectorizer(max_features=5000)
X_train_tfidf = vectorizer.fit_transform(X_train)
X_test_tfidf = vectorizer.transform(X_test)

print("Shape of feature vectors:", X_train_tfidf.shape)

# Convert sparse matrix to dense and discretize
# We'll reduce dimensionality by selecting top features and discretizing
n_features = 10  # Reduce to 10 features for simplicity in Bayesian Network
X_train_dense = X_train_tfidf.toarray()
X_test_dense = X_test_tfidf.toarray()

# Discretize the continuous TF-IDF values into bins
discretizer = KBinsDiscretizer(n_bins=5, encode='ordinal', strategy='uniform')
X_train_discrete = discretizer.fit_transform(X_train_dense[:, :n_features])
X_test_discrete = discretizer.transform(X_test_dense[:, :n_features])

# Create a DataFrame with discrete features and label
feature_names = [f'feature_{i}' for i in range(n_features)]
train_data = pd.DataFrame(X_train_discrete, columns=feature_names)
train_data['label'] = y_train.values

# Define the structure of the Bayesian Network
# Here we'll create a simple structure where all features connect to the label
edges = [(feat, 'label') for feat in feature_names]
model = BayesianNetwork(edges)

# Fit the model using Maximum Likelihood Estimation
model.fit(train_data, estimator=MaximumLikelihoodEstimator)

# Print the learned CPDs (Conditional Probability Distributions)
for cpd in model.get_cpds():
    print(f"CPD of {cpd.variable}:")
    print(cpd)

# Perform inference
inference = VariableElimination(model)

# Make predictions on test set
y_pred = []
test_data = pd.DataFrame(X_test_discrete, columns=feature_names)

for i in range(len(test_data)):
    # Create evidence dictionary for each test instance
    evidence = {feat: int(test_data.iloc[i][feat]) for feat in feature_names}

    # Query the probability of label given evidence
    result = inference.map_query(variables=['label'], evidence=evidence)
    y_pred.append(result['label'])

# Calculate accuracy
accuracy = accuracy_score(y_test, y_pred)
print(f"Model Accuracy: {accuracy:.2f}")

# Example of querying the network
# Take first test instance as an example
example_evidence = {feat: int(test_data.iloc[0][feat]) for feat in feature_names}
print("\nExample inference for first test instance:")
print("Evidence:", example_evidence)
pred = inference.map_query(variables=['label'], evidence=example_evidence)
print("Predicted label:", pred['label'])
print("Actual label:", y_test.iloc[0])

Shape of feature vectors: (20000, 5000)
CPD of feature_0:
+----------------+---------+
| feature_0(0.0) | 0.9982  |
+----------------+---------+
| feature_0(1.0) | 0.00145 |
+----------------+---------+
| feature_0(2.0) | 0.00025 |
+----------------+---------+
| feature_0(3.0) | 5e-05   |
+----------------+---------+
| feature_0(4.0) | 5e-05   |
+----------------+---------+
CPD of label:
+-----------+---------------------+-----+----------------+----------------+
| feature_0 | feature_0(0.0)      | ... | feature_0(4.0) | feature_0(4.0) |
+-----------+---------------------+-----+----------------+----------------+
| feature_1 | feature_1(0.0)      | ... | feature_1(4.0) | feature_1(4.0) |
+-----------+---------------------+-----+----------------+----------------+
| feature_2 | feature_2(0.0)      | ... | feature_2(4.0) | feature_2(4.0) |
+-----------+---------------------+-----+----------------+----------------+
| feature_3 | feature_3(0.0)      | ... | feature_3(4.0) | feature_3(4.0) |
+

0it [00:00, ?it/s]

0it [00:00, ?it/s]

0it [00:00, ?it/s]

0it [00:00, ?it/s]

...

0it [00:00, ?it/s]

0it [00:00, ?it/s]

0it [00:00, ?it/s]

0it [00:00, ?it/s]

0it [00:00, ?it/s]

## Save something

In [ ]:
!git add -A .
!git commit -m "ANN"
!git push

[main d820e65] Decision tree
 1 file changed, 0 insertions(+), 0 deletions(-)
 create mode 100644 ml-course/models/trained/ann_sklearn.joblib
Enumerating objects: 10, done.
Counting objects: 100% (10/10), done.
Delta compression using up to 2 threads
Compressing objects: 100% (6/6), done.
Writing objects: 100% (6/6), 14.57 MiB | 10.06 MiB/s, done.
Total 6 (delta 2), reused 0 (delta 0), pack-reused 0
remote: Resolving deltas: 100% (2/2), completed with 2 local objects.
To https://github.com/khangtruong2252314/ML-BackProg
   4a49d63..d820e65  main -> main
